In [1]:
import sys
import os

#Use if working on Colab
#from google.colab import drive
#drive.mount('/content/drive')
#PATH = '/content/drive/My Drive/PPM_Stability/'

#If working locally
PATH = os.getcwd()
sys.path.append(PATH)

In [2]:
#!pip install lime==0.2.0.1
#!pip install shap==0.37.0
#!pip install xgboost==1.0.0
#!pip install anchor-exp==0.0.2.0

In [3]:
# !pip show acv-exp

In [4]:
import EncoderFactory
#from DatasetManager_for_colab import DatasetManager
from DatasetManager import DatasetManager
import BucketFactory
import stability as st #Nogueira, Sechidis, Brown.

import pandas as pd
import numpy as np
from scipy import stats

from sklearn.metrics import roc_auc_score
from sklearn.pipeline import FeatureUnion, Pipeline
from sklearn.preprocessing import StandardScaler

import time
import os
import sys
from sys import argv
import pickle
from collections import defaultdict
import random
import joblib

from sklearn.ensemble import RandomForestClassifier
import xgboost as xgb
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC

import lime
import lime.lime_tabular
from lime import submodular_pick

#from alibi.utils.data import gen_category_map

from tqdm import tqdm_notebook

#from acv_explainers import ACXplainer
from learning import *
import pyAgrum

import shap

import warnings
warnings.filterwarnings('ignore')

import multiprocessing as mp

2023-08-21 14:44:08.301452: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2023-08-21 14:44:08.301501: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.


RuntimeError: module compiled against API version 0xf but this version of numpy is 0xe

In [5]:
import seaborn as sns
import matplotlib.pyplot as plt
%matplotlib inline

def imp_df(column_names, importances):
        df = pd.DataFrame({'feature': column_names,
                       'feature_importance': importances}) \
           .sort_values('feature_importance', ascending = False) \
           .reset_index(drop = True)
        return df

# plotting a feature importance dataframe (horizontal barchart)
def var_imp_plot(imp_df, title, num_feat):
        imp_df.columns = ['feature', 'feature_importance']
        b= sns.barplot(x = 'feature_importance', y = 'feature', data = imp_df.head(num_feat), orient = 'h', palette="Blues_r")

In [6]:
from lime import submodular_pick

def generate_lime_explanations(explainer,test_xi, cls, submod=False, test_all_data=None, max_feat = 10, scaler=None):
    
    #print("Actual value ", test_y)
    
#     print(type(test_xi))
#     print(type(cls.predict_proba))
#     print(type(max_feat))

    def scale_predict_fn(X):
        scaled_data = scaler.transform(X)
        pred = cls.predict_proba(scaled_data)
        return pred

    def predict_fn(X):
        #X = X.reshape(1, -1)
        pred = cls.predict_proba(X)
        return pred

    if scaler == None:
        exp = explainer.explain_instance(test_xi, 
                                 predict_fn, num_features=max_feat, labels=[0,1])
    else:
        exp = explainer.explain_instance(test_xi, 
                                 scale_predict_fn, num_features=max_feat, labels=[0,1])
        
    return exp
        
    if submod==True:
        sp_obj=submodular_pick.SubmodularPick(explainer, test_all_data, cls.predict_proba, 
                                      sample_size=20, num_features=num_features,num_exps_desired=4)
        [exp.as_pyplot_figure(label=exp.available_labels()[0]) for exp in sp_obj.sp_explanations];

In [7]:
def dispersal(weights, features):
    
    feat_len = len(features)
    weights_by_feat = []
    
    #Weights are sorted by iteration. Transpose list.
    for i in list(range(feat_len)):
        feat_weight = []
        for iteration in weights:
            feat_weight.append(iteration[i])
        weights_by_feat.append(feat_weight)
    
    dispersal = []
    dispersal_no_outlier = []
    
    for each in weights_by_feat:
        #Find mean and variance of weight for each feature
        mean = np.mean(each)
        std_dev = np.std(each)
        var = std_dev**2
        
        #Calculate relative variance, ignore features where the weight is always 0
        if mean == 0:
            dispersal.append(0)
            dispersal_no_outlier.append(0)
        else:
            rel_var = var/abs(mean)
            dispersal.append(rel_var)
            
            #dispersal without outliers - remove anything with a z-score higher
            #than 3 (more than 3 standard deviations away from the mean)
            rem_outlier = []
            z_scores = stats.zscore(each)

            for i in range(len(z_scores)):
                if -3 < z_scores[i] < 3:
                    rem_outlier.append(each[i])
            if rem_outlier != []:
                new_mean = np.mean(rem_outlier)
                if new_mean == 0:
                    dispersal_no_outlier.append(0)
                else:
                    new_std = np.std(rem_outlier)
                    new_var = new_std**2
                    new_rel_var = new_var/abs(new_mean)
                    dispersal_no_outlier.append(new_rel_var)
            else:
                dispersal_no_outlier.append(rel_var)

    return dispersal, dispersal_no_outlier

In [8]:
def create_samples(shap_explainer, iterations, row, features, pred, top = None, scaler = None):
    length = len(features)
    
    exp = []
    rel_exp = []
    
    if scaler != None:
        row = scaler.transform(row)
    
    for j in range(iterations):
        #Generate shap values for row
        if type(shap_explainer) == shap.explainers._tree.Tree:
            shap_values = shap_explainer(row, check_additivity = False).values
        elif type(shap_explainer) == shap.explainers._permutation.Permutation:
            shap_values = shap_explainer(row.reshape(1, -1), max_evals = 2*length+1).values
        else:
            shap_values = shap_explainer(row.reshape(1, -1)).values
        
        #print(exp.shape)
        #print(exp)
        #print(shap_values.shape)
        #print(len(features))
        if shap_values.shape == (1, len(features), 2):
            shap_values = shap_values[0]
            
        #print(exp.shape)
        
        if shap_values.shape == (len(features), 2):
            shap_values = np.array([feat[pred] for feat in shap_values]).reshape(len(features))
        elif shap_values.shape == (1, len(row)) or shap_values.shape == (len(features), 1):
            shap_values = shap_values.reshape(len(features))
            
        #print(np.array(exp).shape)
        
        if scaler != None:
            #print(shap_values)
            shap_values = scaler.inverse_transform(shap_values.reshape(1, -1))[0]
            #print(shap_values.shape)
        
        #Map SHAP values to feature names
        importances = []
        
        abs_values = []
    
        for i in range(length):
            feat = features[i]
            shap_val = shap_values[i]
            abs_val = abs(shap_values[i])
            entry = (feat, shap_val, abs_val)
            importances.append(entry)
            abs_values.append(abs_val)
        
        #Sort features by influence on result
        importances.sort(key=lambda tup: tup[2], reverse = True)
        
        #Create list of all feature
        exp.append(importances)
        
        #print(exp[0])
        
        #Create list of most important features
        rel_feat = []
        if top != None:
            for i in range(top):
                feat = importances[i]
                if feat[2] > 0:
                    rel_feat.append(feat)

            rel_exp.append(rel_feat)
        else:
            bins = pd.cut(abs_values, 4, duplicates = "drop", retbins = True)[-1]
            q1_min = bins[-2]
            rel_feat = [feat for feat in importances if feat[2] >= q1_min]
            rel_exp.append(rel_feat)
        
    return exp, rel_exp

In [9]:
def get_acv_features(explainer, instance, cls, X_train, y_train, exp_iter):
    instance = instance.reshape(1, -1)
    y = cls.predict(instance)
    
    t=np.var(y_train)

    feats = []
    feat_imp = []

    for i in range(exp_iter):
        sufficient_expl, sdp_expl, sdp_global = explainer.sufficient_expl_rf(instance, y, X_train, y_train,
                                                                                 t=t, pi_level=0.8)
        clean_expl = sufficient_expl.copy()
        clean_expl = clean_expl[0]
        clean_expl = [sublist for sublist in clean_expl if sum(n<0 for n in sublist)==0 ]

        clean_sdp = sdp_expl[0].copy()
        clean_sdp = [sdp for sdp in clean_sdp if sdp > 0]
        
        lximp = explainer.compute_local_sdp(X_train.shape[1], clean_expl)
        feat_imp.append(lximp)
        
        if len(clean_expl)==0 or len(clean_expl[0])==0:
            print("No explamation meets pi level")
        else:
            lens = [len(i) for i in clean_expl]
            me_loc = [i for i in range(len(lens)) if lens[i]==min(lens)]
            mse_loc = np.argmax(np.array(clean_sdp)[me_loc])
            mse = np.array(clean_expl)[me_loc][mse_loc]
            feats.extend(mse)

    if len(feats)==0:
        feat_pos = []
    else:
        feat_pos = set(feats)
    
      
    feat_imp = np.mean(feat_imp, axis=0)
    
    return feat_imp, feat_pos

In [10]:
def get_linda_features(instance, cls, scaler, dataset, exp_iter, feat_list, percentile):
    label_lst = ["Negative", "Positive"]
    
    feat_pos = []
    lkhoods = []
    
    save_to = os.path.join(PATH, dataset, cls_method, method_name)+"/"
    
    for i in range(exp_iter):
        [bn, inference, infoBN] = generate_BN_explanations(instance, label_lst, feat_list, "Result", 
                                                           None, scaler, cls, save_to, dataset, show_in_notebook = False,
                                                           samples=round(len(feat_list)*2))
        
        ie = pyAgrum.LazyPropagation(bn)
        result_posterior = ie.posterior(bn.idFromName("Result")).topandas()
        if len(result_posterior.shape)==1:
            result_proba = result_posterior.values[0]
        else:
            result_proba = result_posterior.loc["Result", label_lst[instance['predictions']]]        
        row = instance['original_vector']
        #print(row)

        likelihood = [0]*len(feat_list)

        for j in range(len(feat_list)):
            var_labels = bn.variable(feat_list[j]).labels()
            str_bins = list(var_labels)
            bins = []

            for disc_bin in str_bins:
                disc_bin = disc_bin.strip('"(]')
                cat = [float(val) for val in disc_bin.split(',')]
                bins.append(cat)

            feat_bin = None
            val = row[j]
            
            #Find appropriate bin, if higher or lower than bins,
            #use first or last bin
            for k in range(len(bins)):
                if k == 0 and val <= bins[k][0]:
                    feat_bin = str_bins[k]
                elif k == len(bins)-1 and val >= bins[k][1]:
                    feat_bin = str_bins[k]
                elif val > bins[k][0] and val <= bins[k][1]:
                    feat_bin = str_bins[k]

            #If the value doesn't fit into any bin,
            #pick the nearest
            if feat_bin == None: 
                bins_diff = np.array(bins) - val
                inds = np.unravel_index(np.abs(bins_diff).argmin(axis=None), bins_diff.shape)
                k = inds[0]
                feat_bin = str_bins[k]
            
            result_posterior = ie.posterior(bn.idFromName("Result")).topandas()
            if len(result_posterior.shape)==1:
                new_proba = result_posterior.values[0]
            else:
                new_proba = result_posterior.loc["Result", label_lst[instance['predictions']]]
            #print(result_proba, new_proba)
            proba_change = result_proba-new_proba
            likelihood[j] = abs(proba_change)

        lkhoods.append(likelihood)
        
    min_coef = min( np.mean(lkhoods, axis=0))
    max_coef = max( np.mean(lkhoods, axis=0))
    
    k = (max_coef-min_coef)*percentile
    q1_min = max_coef - k

    #If fixing all features produces the same result for the class,
    #return all features
    if len(set(np.mean(lkhoods, axis=0)))==1:
        feat_pos.extend(range(len(feat_list)))
    else:
        feat_pos.extend(list(np.where(np.mean(lkhoods, axis=0) >= q1_min)[0]))

    feat_pos = set(feat_pos)
        
    return np.mean(lkhoods, axis=0), feat_pos

In [11]:
dataset_ref = "bpic2012"
params_dir = PATH + "params"
results_dir = "results"
bucket_method = "single"
cls_encoding = "agg"
cls_method = "logit"

gap = 1
n_iter = 1

method_name = "%s_%s"%(bucket_method, cls_encoding)
save_to = os.path.join(PATH, dataset_ref, cls_method, method_name)

xai_method = "LINDA"

sample_size = 2
exp_iter = 5
max_feat = 10
max_prefix = 20
random_state = 22

dataset_ref_to_datasets = {
    "bpic2012" : ["bpic2012_accepted"],
    "sepsis_cases": ["sepsis_cases_1"],
    "production" : ["production"],
    "bpic2011": ["bpic2011_f1"],
    "hospital": ["hospital_billing_2"],
    "traffic": ["traffic_fines_1"]
}

datasets = [dataset_ref] if dataset_ref not in dataset_ref_to_datasets else dataset_ref_to_datasets[dataset_ref]

datasets

['bpic2012_accepted']

In [12]:
# for dataset_name in datasets:

#     min_prefix_length = 1
#     max_prefix_length = max_prefix

#     dataset_manager = DatasetManager(dataset_name)
#     #data = dataset_manager.read_dataset()

#     all_pipelines = []
#     all_cls = []
#     all_encoders = []
#     all_scalers = []
#     all_train = []
#     all_samples = []
#     all_results = []

#     dt_val_prefixes = pd.read_csv(os.path.join(PATH, "%s/datasets/val_prefixes.csv" %(dataset_ref)))
#     dt_train_prefixes = pd.read_csv(os.path.join(PATH, "%s/datasets/val_prefixes.csv" %(dataset_ref)))
#     dt_train_prefixes = pd.concat([dt_train_prefixes, dt_val_prefixes])
#     dt_train_prefixes = dataset_manager.generate_prefix_data(dt_train_prefixes, min_prefix_length, max_prefix_length)

#     if bucket_method == "state":
#         bucket_encoding = "last"
#     else:
#         bucket_encoding = "agg"
    
#     bucketer_args = {'encoding_method':bucket_encoding,
#                      'case_id_col':dataset_manager.case_id_col, 
#                      'cat_cols':[dataset_manager.activity_col], 
#                      'num_cols':[], 
#                      'random_state':random_state}

#     bucketer = BucketFactory.get_bucketer(bucket_method, **bucketer_args)
#     bucket_assignments_train = bucketer.fit_predict(dt_train_prefixes)
    
#     for ii in range(n_iter):
#         num_buckets = len([name for name in os.listdir(os.path.join(PATH,'%s/%s/%s/pipelines'% (dataset_ref, cls_method, method_name)))])

#         for bucket in tqdm_notebook(range(num_buckets)):
#             bucketID = bucket+1
#             print ('Bucket', bucketID)

#             #import everything needed to sort and predict
#             pipeline_path = os.path.join(PATH, "%s/%s/%s/pipelines/pipeline_bucket_%s.joblib" % 
#                                          (dataset_ref, cls_method, method_name, bucketID))
#             pipeline = joblib.load(pipeline_path)
#             feature_combiner = pipeline['encoder']
#             if 'scaler' in pipeline.named_steps:
#                 scaler = pipeline['scaler']
#             else:
#                 scaler = None
#             cls = pipeline['cls']
            
#             all_cls.append(cls)
#             all_encoders.append(feature_combiner)
#             all_scalers.append(scaler)
#             all_pipelines.append(pipeline)

#             #find relevant samples for bucket
#             bucket_sample = pd.read_csv(os.path.join(PATH, "%s/%s/%s/samples/test_sample_bucket_%s.csv" % 
#                                       (dataset_ref, cls_method, method_name, bucketID))).values
#             results_template = pd.read_csv(os.path.join(PATH, "%s/%s/%s/samples/results_bucket_%s.csv" % 
#                                       (dataset_ref, cls_method, method_name, bucketID)))
    
#             if scaler != None:
#                 bucket_sample = scaler.transform(bucket_sample)
#             bucket_results = results_template
            
#             feat_names = feature_combiner.get_feature_names()
#             feat_list = [feat.replace(" ", "_") for feat in feat_names]
            
#             all_samples.append(bucket_sample)
#             all_results.append(bucket_results)
            
#             #import training data for bucket
#             train_data = pd.read_csv(os.path.join(PATH, "%s/%s/%s/train_data/train_data_bucket_%s.csv" % 
#                                                           (dataset_ref, cls_method, method_name, bucketID))).values
#             if scaler != None:
#                 train_data = scaler.transform(train_data)
            
#             all_train.append(train_data)
            
#             #get target values for bucket
#             train_prefixes = pd.read_csv

In [13]:
def shap_eval(instance):
    #instance_no += 1    
    #print("Testing", instance_no, "of", len(sample_instances), ".")

    #if cls_method == "xgboost":
    instance = instance.reshape(1, -1)
    pred = cls.predict(instance)

    #Get Tree SHAP explanations for instance
    exp, rel_exp = create_samples(shap_explainer, exp_iter, instance, feat_list, pred, scaler = scaler)

    feat_pres = []
    feat_weights = []

    for iteration in rel_exp:
        #print("Computing feature presence for iteration", rel_exp.index(iteration))

        presence_list = [0]*len(feat_list)

        for each in feat_list:
            list_idx = feat_list.index(each)

            for explanation in iteration:
                if each in explanation[0]:
                    presence_list[list_idx] = 1

        feat_pres.append(presence_list)

    for iteration in exp:
        #print("Compiling feature weights for iteration", exp.index(iteration))

        weights = [0]*len(feat_list)

        for each in feat_list:
            list_idx = feat_list.index(each)

            for explanation in iteration:
                if each in explanation[0]:

                    weights[list_idx] = explanation[1]
        feat_weights.append(weights)

    stability = st.getStability(feat_pres)
    #print ("Stability:", round(stability,2))
    #subset_stability.append(stability)

    rel_var, second_var = dispersal(feat_weights, feat_list)
    avg_dispersal = 1-np.mean(rel_var)
    #print ("Dispersal of feature importance:", round(avg_dispersal, 2))
    #weight_stability.append(avg_dispersal)
    adj_dispersal = 1-np.mean(second_var)
    #print ("Dispersal with no outliers:", round(adj_dispersal, 2))
    #adjusted_weight_stability.append(adj_dispersal)
    
    return stability, avg_dispersal, adj_dispersal

In [14]:
all_results = []

if xai_method=="SHAP":

    for dataset_name in datasets:
        
        for ii in range(n_iter):
            num_buckets = len([name for name in os.listdir(os.path.join(PATH,'%s/%s/%s/pipelines'% 
                                                                        (dataset_ref, cls_method, method_name)))])
            
            for bucket in tqdm_notebook(range(num_buckets)):
                bucketID = bucket+1
                print ('Bucket', bucketID)
                
                #import everything needed to sort and predict
                pipeline_path = os.path.join(PATH, save_to, "pipelines/pipeline_bucket_%s.joblib" % 
                                             (bucketID))
                pipeline = joblib.load(pipeline_path)
                feature_combiner = pipeline['encoder']
                if 'scaler' in pipeline.named_steps:
                    scaler = pipeline['scaler']
                else:
                    scaler = None
                cls = pipeline['cls']
                
                #import training data for bucket
                trainingdata = pd.read_csv(os.path.join(PATH, "%s/%s/%s/train_data/train_data_bucket_%s.csv" % 
                                                              (dataset_ref, cls_method, method_name, bucketID))).values
                targets = pd.read_csv(os.path.join(PATH, "%s/%s/%s/train_data/y_train_bucket_%s.csv" % 
                                                              (dataset_ref, cls_method, method_name, bucketID))).values
                if scaler != None:
                    trainingdata = scaler.transform(trainingdata)
                    
                #find relevant samples for bucket
                sample_instances = pd.read_csv(os.path.join(PATH, "%s/%s/%s/samples/test_sample_bucket_%s.csv" % 
                                          (dataset_ref, cls_method, method_name, bucketID))).values
                results = pd.read_csv(os.path.join(PATH, "%s/%s/%s/samples/results_bucket_%s.csv" % 
                                          (dataset_ref, cls_method, method_name, bucketID)), sep=";")
                
                if scaler != None:
                    sample_instances = scaler.transform(sample_instances)
                
                #create explanation mechanism
                if cls_method == "xgboost" or cls_method == "decision_tree":
                    shap_explainer = shap.Explainer(cls)
                elif cls_method == "nb":
                    shap_explainer = shap.Explainer(cls.predict_proba, trainingdata)
                else:
                    shap_explainer = shap.Explainer(cls, trainingdata)
                print(type(shap_explainer))
                
                #Identify feature names
                feat_list = [feat.replace(" ", "_") for feat in feature_combiner.get_feature_names()]
                                    
                #explain the chosen instances and find the stability score
                pool = mp.Pool(mp.cpu_count())
                start = time.time()
                stability, avg_dispersal, adj_dispersal = zip(*pool.map(shap_eval, [instance for instance in sample_instances]))
                print(time.time()-start, "seconds")
                    
                subset_stability = list(stability)
                weight_stability = list(avg_dispersal)
                adjusted_weight_stability = list(adj_dispersal)
                    
                results["SHAP Subset Stability"] = subset_stability
                results["SHAP Weight Stability"] = weight_stability
                results["SHAP Adjusted Weight Stability"] = adjusted_weight_stability
#                 results.to_csv(os.path.join(PATH,"%s/%s/%s/samples/results_bucket_%s.csv") % 
#                                (dataset_ref, cls_method, method_name, bucketID), sep=";", index=False)
                
                all_results.append(results)

In [15]:
def lime_eval(instance):
    #Get lime explanations for instance
    feat_pres = []
    feat_weights = []

    for iteration in list(range(exp_iter)):

        lime_exp = generate_lime_explanations(lime_explainer, instance, cls,
                                              max_feat = len(feat_list), scaler = scaler)

        all_weights = [exp[1] for exp in lime_exp.as_list()]
        bins = pd.cut(all_weights, 4, duplicates = "drop", retbins = True)[-1]
        q1_min = bins[-2]

        presence_list = [0]*len(feat_list)
        weights = [0]*len(feat_list)

        for each in feat_list:
            list_idx = feat_list.index(each)
            #print ("Feature", list_idx)
            for explanation in lime_exp.as_list():
                if each in explanation[0]:
                    if explanation[1] >= q1_min:
                        presence_list[list_idx] = 1
                    weights[list_idx] = explanation[1]

        feat_pres.append(presence_list)
        feat_weights.append(weights)

    stability = st.getStability(feat_pres)
#     print ("Stability:", round(stability,2))
#     subset_stability.append(stability)

    rel_var, second_var = dispersal(feat_weights, feat_list)
    avg_dispersal = 1-np.mean(rel_var)
#     print ("Dispersal of feature importance:", round(avg_dispersal, 2))
#     weight_stability.append(avg_dispersal)
    adj_dispersal = 1-np.mean(second_var)
#     print ("Dispersal with no outliers:", round(adj_dispersal, 2))
#     adjusted_weight_stability.append(adj_dispersal)

    return stability, avg_dispersal, adj_dispersal


In [16]:
if xai_method=="LIME":
    print("evaluating LIME")

    for dataset_name in datasets:
        
        num_buckets = len([name for name in os.listdir(os.path.join(PATH,'%s/%s/%s/pipelines'% 
                                                                    (dataset_ref, cls_method, method_name)))])
        dataset_manager = DatasetManager(dataset_name)

        for bucket in tqdm_notebook(range(num_buckets)):
            bucketID = bucket+1
            print ('Bucket', bucketID)
            
           #import everything needed to sort and predict
            pipeline_path = os.path.join(PATH, save_to, "pipelines/pipeline_bucket_%s.joblib" % 
                                         (bucketID))
            pipeline = joblib.load(pipeline_path)
            feature_combiner = pipeline['encoder']
            if 'scaler' in pipeline.named_steps:
                scaler = pipeline['scaler']
            else:
                scaler = None
            cls = pipeline['cls']

            #import training data for bucket
            trainingdata = pd.read_csv(os.path.join(PATH, "%s/%s/%s/train_data/train_data_bucket_%s.csv"%(dataset_ref, cls_method, method_name, bucketID))).values
            targets = pd.read_csv(os.path.join(PATH, "%s/%s/%s/train_data/y_train_bucket_%s.csv"%(dataset_ref, cls_method, method_name, bucketID))).values
            if scaler != None:
                trainingdata = scaler.transform(trainingdata)

            #find relevant samples for bucket
            sample_instances = pd.read_csv(os.path.join(PATH, "%s/%s/%s/samples/test_sample_bucket_%s.csv" % (dataset_ref, cls_method, method_name, bucketID))).values
            results = pd.read_csv(os.path.join(PATH, "%s/%s/%s/samples/results_bucket_%s.csv" % (dataset_ref, cls_method, method_name, bucketID)))
            
            if scaler != None:
                sample_instances = scaler.transform(sample_instances)

            feat_list = [feat.replace(" ", "_") for feat in feature_combiner.get_feature_names()]
            class_names = ["Negative", "Positive"]
            
            cats = [feat for col in dataset_manager.dynamic_cat_cols+dataset_manager.static_cat_cols 
                    for feat in range(len(feat_list)) if col in feat_list[feat]]

            #create explainer now that can be passed later
            lime_explainer = lime.lime_tabular.LimeTabularExplainer(trainingdata,
                                  feature_names = feat_list, class_names=class_names, categorical_features = cats)
            
            #explain the chosen instances and find the stability score
            pool = mp.Pool(mp.cpu_count())
            start = time.time()
            stability, avg_dispersal, adj_dispersal = zip(*pool.map(lime_eval, [instance for instance in sample_instances[:5]]))
            print(time.time()-start, "seconds")

            subset_stability = list(stability)
            weight_stability = list(avg_dispersal)
            adjusted_weight_stability = list(adj_dispersal)
               
            results["LIME Subset Stability"] = subset_stability
            results["LIME Weight Stability"] = weight_stability
            results["LIME Adjusted Weight Stability"] = adjusted_weight_stability
            #results.to_csv(os.path.join(PATH,"%s/%s/%s/samples/results_bucket_%s.csv") % 
            #                   (dataset_ref, cls_method, method_name, bucketID), sep=";", index=False)
                
            all_results.append(results)

In [17]:
def acv_eval(instance):
    #Get acv explanations for instance
    feat_pres = []
    feat_weights = []

    for iteration in list(range(exp_iter)):
        weights, feat_pos = get_acv_features(acv_explainer, instance, cls, trainingdata, targets, 1)
        print(weights)
        print(feat_pos)

        presence_list = np.array([0]*len(feat_list))                    
        presence_list[feat_pos] = 1

        feat_pres.append(presence_list)
        feat_weights.append(weights)

    stability = st.getStability(feat_pres)
    #print ("Stability:", round(stability,2))
    subset_stability.append(stability)

    rel_var, second_var = dispersal(feat_weights, feat_list)
    avg_dispersal = 1-np.mean(rel_var)
    #print ("Dispersal of feature importance:", round(avg_dispersal, 2))
    weight_stability.append(avg_dispersal)
    adj_dispersal = 1-np.mean(second_var)
    #print ("Dispersal with no outliers:", round(adj_dispersal, 2))
    adjusted_weight_stability.append(adj_dispersal)

    
    return stability, avg_dispersal, adj_dispersal

In [18]:
if xai_method=="ACV":

    for dataset_name in datasets:
        
        num_buckets = len([name for name in os.listdir(os.path.join(PATH,'%s/%s/%s/pipelines'% 
                                                                    (dataset_ref, cls_method, method_name)))])
        dataset_manager = DatasetManager(dataset_name)

        for bucket in tqdm_notebook(range(num_buckets)):
            bucketID = bucket+1
            print ('Bucket', bucketID)
            
            #import everything needed to sort and predict
            pipeline_path = os.path.join(PATH, save_to, "pipelines/pipeline_bucket_%s.joblib" % 
                                         (bucketID))
            pipeline = joblib.load(pipeline_path)
            feature_combiner = pipeline['encoder']
            if 'scaler' in pipeline.named_steps:
                scaler = pipeline['scaler']
            else:
                scaler = None
            cls = pipeline['cls']

            #import training data for bucket
            trainingdata = pd.read_csv(os.path.join(PATH, "%s/%s/%s/train_data/train_data_bucket_%s.csv" % 
                                                          (dataset_ref, cls_method, method_name, bucketID))).values
            targets = pd.read_csv(os.path.join(PATH, "%s/%s/%s/train_data/y_train_bucket_%s.csv" % 
                                                          (dataset_ref, cls_method, method_name, bucketID))).values
            if scaler != None:
                trainingdata = scaler.transform(trainingdata)

            #find relevant samples for bucket
            sample_instances = pd.read_csv(os.path.join(PATH, "%s/%s/%s/samples/test_sample_bucket_%s.csv" % 
                                      (dataset_ref, cls_method, method_name, bucketID))).values
            results = pd.read_csv(os.path.join(PATH, "%s/%s/%s/samples/results_bucket_%s.csv" % 
                                      (dataset_ref, cls_method, method_name, bucketID)))
            
            if scaler != None:
                sample_instances = scaler.transform(sample_instances)
            
            acv_explainer = joblib.load(os.path.join(PATH,'%s/%s/%s/acv_surrogate/acv_explainer_bucket_%s.joblib'% 
                                                                    (dataset_ref, cls_method, method_name, bucketID)))

            feat_list = [feat.replace(" ", "_") for feat in feature_combiner.get_feature_names()]
#             class_names = ["Negative", "Positive"]
            
#             cats = [feat for col in dataset_manager.dynamic_cat_cols+dataset_manager.static_cat_cols 
#                     for feat in range(len(feat_list)) if col in feat_list[feat]]

            subset_stability = []
            weight_stability = []
            adjusted_weight_stability = []

            #create explainer now that can be passed later
#             lime_explainer = lime.lime_tabular.LimeTabularExplainer(trainingdata,
#                                   feature_names = feat_list, class_names=class_names, categorical_features = cats)
            
            instance_no = 0
            print(len(sample_instances))
#             #explain the chosen instances and find the stability score
#             for instance in tqdm_notebook(sample_instances[:5]):
#                 instance_no += 1

#                 print("Testing", instance_no, "of", len(sample_instances), ".")
                
#                 stability, avg_dispersal, adj_dispersal = acv_eval(instance)

            #explain the chosen instances and find the stability score
            pool = mp.Pool(mp.cpu_count())
            start = time.time()
            stability, avg_dispersal, adj_dispersal = zip(*pool.map(acv_eval, [instance for instance in sample_instances[:5]]))
            print(time.time()-start, "seconds")

            subset_stability = list(stability)
            weight_stability = list(avg_dispersal)
            adjusted_weight_stability = list(adj_dispersal)
                
            results["ACV Subset Stability"] = subset_stability
            results["ACV Weight Stability"] = weight_stability
            results["ACV Adjusted Weight Stability"] = adjusted_weight_stability
#             results.to_csv(os.path.join(PATH,"%s/%s/%s/samples/results_bucket_%s.csv") % 
#                                (dataset_ref, cls_method, method_name, bucketID), sep=";", index=False)                
#                 all_results.append(results)

In [19]:
def linda_eval(instance):
    #Get lime explanations for instance
    feat_pres = []
    feat_weights = []



    for iteration in list(range(exp_iter)):
        weights, feat_pos = get_linda_features(instance, cls, scaler, dataset_ref, 1, feat_list, 1)
        #print(weights)
        #print(feat_pos)

        feat_pos = list(feat_pos)

        #bins = pd.cut(weights, 4, duplicates = "drop", retbins = True)[-1]
        #q1_min = bins[-2]

        presence_list = np.array([0]*len(feat_list))                    

        presence_list[feat_pos] = 1

        feat_pres.append(presence_list)
        feat_weights.append(weights)

    #print(feat_pres)
    #print(feat_weights)

    stability = st.getStability(feat_pres)
    print ("Stability:", round(stability,2))
    subset_stability.append(stability)

    rel_var, second_var = dispersal(feat_weights, feat_list)
    avg_dispersal = 1-np.mean(rel_var)
    print ("Dispersal of feature importance:", round(avg_dispersal, 2))
    weight_stability.append(avg_dispersal)
    adj_dispersal = 1-np.mean(second_var)
    print ("Dispersal with no outliers:", round(adj_dispersal, 2))
    adjusted_weight_stability.append(adj_dispersal)
    
    return stability, avg_dispersal, adj_dispersal

In [20]:
if xai_method=="LINDA":

    for dataset_name in datasets:
        
        num_buckets = len([name for name in os.listdir(os.path.join(PATH,'%s/%s/%s/pipelines'% 
                                                                    (dataset_ref, cls_method, method_name)))])
        dataset_manager = DatasetManager(dataset_name)

        for bucket in tqdm_notebook(range(num_buckets)):
            bucketID = bucket+1
            print ('Bucket', bucketID)
            
            #import everything needed to sort and predict
            pipeline_path = os.path.join(PATH, save_to, "pipelines/pipeline_bucket_%s.joblib" % 
                                         (bucketID))
            pipeline = joblib.load(pipeline_path)
            feature_combiner = pipeline['encoder']
            if 'scaler' in pipeline.named_steps:
                scaler = pipeline['scaler']
            else:
                scaler = None
            cls = pipeline['cls']

            #import training data for bucket
            trainingdata = pd.read_csv(os.path.join(PATH, "%s/%s/%s/train_data/train_data_bucket_%s.csv" % 
                                                          (dataset_ref, cls_method, method_name, bucketID))).values
            targets = pd.read_csv(os.path.join(PATH, "%s/%s/%s/train_data/y_train_bucket_%s.csv" % 
                                                          (dataset_ref, cls_method, method_name, bucketID))).values
            if scaler != None:
                trainingdata = scaler.transform(trainingdata)

            #find relevant samples for bucket
            sample_instances = pd.read_csv(os.path.join(PATH, "%s/%s/%s/samples/test_sample_bucket_%s.csv" % 
                                      (dataset_ref, cls_method, method_name, bucketID))).values
            results = pd.read_csv(os.path.join(PATH, "%s/%s/%s/samples/results_bucket_%s.csv" % 
                                      (dataset_ref, cls_method, method_name, bucketID)), sep=";")
            
            if scaler != None:
                sample_instances = scaler.transform(sample_instances)

            test_dict = generate_local_predictions( sample_instances, results["Actual"], cls, scaler, None )

            feat_list = [feat.replace(" ", "_") for feat in feature_combiner.get_feature_names()]
#             class_names = ["Negative", "Positive"]
            
#             cats = [feat for col in dataset_manager.dynamic_cat_cols+dataset_manager.static_cat_cols 
#                     for feat in range(len(feat_list)) if col in feat_list[feat]]

            subset_stability = []
            weight_stability = []
            adjusted_weight_stability = []

            #create explainer now that can be passed later
#             lime_explainer = lime.lime_tabular.LimeTabularExplainer(trainingdata,
#                                   feature_names = feat_list, class_names=class_names, categorical_features = cats)
            
            instance_no = 0
            print(len(sample_instances))
            #explain the chosen instances and find the stability score
            pool = mp.Pool(mp.cpu_count())
            start = time.time()
            stability, avg_dispersal, adj_dispersal = zip(*pool.map(linda_eval, [instance for instance in test_dict[:5]]))
            print(time.time()-start, "seconds")

            subset_stability = list(stability)
            weight_stability = list(avg_dispersal)
            adjusted_weight_stability = list(adj_dispersal)
                

#             results["LINDA Subset Stability"] = subset_stability
#             results["LINDA Weight Stability"] = weight_stability
#             results["LINDA Adjusted Weight Stability"] = adjusted_weight_stability
#             results.to_csv(os.path.join(PATH,"%s/%s/%s/samples/results_bucket_%s.csv") % 
#                                (dataset_ref, cls_method, method_name, bucketID), sep=";", index=False)                
#             all_results.append(results)
            
# pd.concat(all_results).to_csv(os.path.join(PATH,"%s/%s/%s/samples/results.csv") % (dataset_ref, cls_method, method_name), 
#                               sep=";", index=False)

  0%|          | 0/1 [00:00<?, ?it/s]

Bucket 1
112
Selecting Greedy Hill Climbing AlgorithmSelecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing AlgorithmSelecting Greedy Hill Climbing Algorithm


Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing AlgorithmSelecting Greedy Hill Climbing Algorithm

Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing Algorithm
Sta

In [21]:
start_time = time.time()
for instance in test_dict[:5]:
    linda_eval(instance)
print(time.time()-start_time, "seconds")

Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing Algorithm
Stability: nan
Dispersal of feature importance: 1.0
Dispersal with no outliers: 1.0
Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing Algorithm
Stability: nan
Dispersal of feature importance: 1.0
Dispersal with no outliers: 1.0
Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing Algorithm
Stability: nan
Dispersal of feature importance: 1.0
Dispersal with no outliers: 1.0
Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing Algorithm
Selecting Greedy Hill Climbing Algorithm
Selecting 

In [22]:
results

Case ID  Actual  Prefix Length  Prediction  Prediction Probability  \
0      204484       0              1           0                0.523042   
1      204718       1              1           0                0.523000   
2      204969       0              1           0                0.546811   
3      206546       1              1           0                0.519289   
4      208619       1              1           0                0.518807   
..        ...     ...            ...         ...                     ...   
107  213468_3       1              3           0                0.533265   
108  213705_9       0              9           0                0.511271   
109  213906_2       1              2           0                0.522326   
110  213954_6       0              6           0                0.608060   
111  214142_4       0              4           0                0.535227   

     SHAP Subset Stability  SHAP Weight Stability  \
0                      1.0                    1.0   
1                      1.0                    1.0   
2                      1.0                    1.0   
3                      1.0                    1.0   
4                      1.0                    1.0   
..                     ...                    ...   
107                    1.0                    1.0   
108                    1.0                    1.0   
109                    1.0                    1.0   
110                    1.0                    1.0   
111                    1.0                    1.0   

     SHAP Adjusted Weight Stability  LIME Subset Stability  \
0                               1.0              -0.148639   
1                               1.0              -0.171724   
2                               1.0               1.000000   
3                               1.0               1.000000   
4                               1.0               1.000000   
..                              ...                    ...   
107                             1.0               1.000000   
108                             1.0              -0.152522   
109                             1.0               1.000000   
110                             1.0              -0.177518   
111                             1.0               1.000000   

     LIME Weight Stability  LIME Adjusted Weight Stability  \
0                 0.997318                        0.997318   
1                 0.997763                        0.997763   
2                 0.998074                        0.998074   
3                 0.998255                        0.998255   
4                 0.996912                        0.996912   
..                     ...                             ...   
107               0.997988                        0.997988   
108               0.994363                        0.994363   
109               0.997823                        0.997823   
110               0.997451                        0.997451   
111               0.998239                        0.998239   

     ACV Subset Stability  ACV Weight Stability  \
0                     NaN                   1.0   
1                     NaN                   1.0   
2                     NaN                   1.0   
3                     NaN                   1.0   
4                     NaN                   1.0   
..                    ...                   ...   
107                   NaN                   1.0   
108                   NaN                   1.0   
109                   NaN                   1.0   
110                   NaN                   1.0   
111                   NaN                   1.0   

     ACV Adjusted Weight Stability  LINDA Subset Stability  \
0                              1.0                     1.0   
1                              1.0                     1.0   
2                              1.0                     1.0   
3                              1.0                     1.0   
4                              1.0         

In [23]:
get_linda_features(instance, cls, scaler, dataset_ref, 1, feat_list, 1)

Selecting Greedy Hill Climbing Algorithm


(array([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0.]),
 {0,
  1,
  2,
  3,
  4,
  5,
  6,
  7,
  8,
  9,
  10,
  11,
  12,
  13,
  14,
  15,
  16,
  17,
  18,
  19,
  20,
  21,
  22,
  23,
  24,
  25,
  26,
  27,
  28,
  29,
  30,
  31,
  32,
  33,
  34,
  35,
  36,
  37,
  38,
  39,
  40,
  41,
  42,
  43,
  44,
  45,
  46,
  47,
  48,
  49,
  50,
  51,
  52,
  53,
  54,
  55,
  56,
  57,
  58,
  59,
  60,
  61,
  62,
  63,
  64,
  65,
  66,
  67,
  68,
  69,
  70,
  71,
  72,
  73,
  74,
  75,
  76,
  

In [24]:
label_lst = ["Negative", "Positive"]
    
feat_pos = []
lkhoods = []

save_to = os.path.join(PATH, dataset_ref, cls_method, method_name)+"/"

[bn, inference, infoBN] = generate_BN_explanations(instance, label_lst, feat_list, "Result", 
                                                       None, scaler, cls, save_to, dataset_ref, show_in_notebook = False,
                                                       samples=round(len(feat_list)*1.5))

Selecting Greedy Hill Climbing Algorithm


In [25]:
ie = pyAgrum.LazyPropagation(bn)
result_posterior = ie.posterior(bn.idFromName("Result")).topandas()

if len(result_posterior.shape)==1:
    result_proba = result_posterior.values[0]
else:
    result_proba = result_posterior.loc["Result", label_lst[instance['predictions']]]

row = instance['original_vector']


In [26]:
for j in range(len(feat_list)):
            var_labels = bn.variable(feat_list[j]).labels()
            str_bins = list(var_labels)
            bins = []
            
            for disc_bin in str_bins:
                disc_bin = disc_bin.strip('"(]')
                cat = [float(val) for val in disc_bin.split(',')]
                bins.append(cat)
            
            feat_bin = None
            val = row[j]
            
            #Find appropriate bin, if higher or lower than bins,
            #use first or last bin
            for k in range(len(bins)):
                if k == 0 and val <= bins[k][0]:
                    feat_bin = str_bins[k]
                elif k == len(bins)-1 and val >= bins[k][1]:
                    feat_bin = str_bins[k]
                elif val > bins[k][0] and val <= bins[k][1]:
                    feat_bin = str_bins[k]

            #If the value doesn't fit into any bin,
            #pick the nearest
            if feat_bin == None: 
                bins_diff = np.array(bins) - val
                inds = np.unravel_index(np.abs(bins_diff).argmin(axis=None), bins_diff.shape)
                k = inds[0]
                feat_bin = str_bins[k]
                
#                print(bins_diff)
#                 for k in range(len(bins)):
#                     if k!=len(bins)-1 and bins[k+1][0]-bins[k][1]!=0:
#                         print("Gap between bins")
#                         lower = val - bins[k][1]
#                         higher = bins[k+1][0] - val
#                         if lower > higher:
#                             feat_bin = str_bins[k+1]
#                         else:
#                             feat_bin = str_bins[k]
#                 if feat_bin==None:
#                     print("Some other issue with bins")
                    
            print(val)
            #print(row[j])
            print(str_bins[k])

            ie = pyAgrum.LazyPropagation(bn)
            ie.setEvidence({feat_list[j]: feat_bin})
            ie.makeInference()

27000.0
"(10397.57, 49601.58]"
0.0
"(0.024, 0.23]"
0.0
"(0.12, 0.23]"
0.0
"(-0.01, 0.2]"
0.0
"(0.011, 0.21]"
0.0
"(-0.01, 0.059]"
0.0
"(-0.01, 0.12]"
1.0
"(1.16, 1.17]"
0.0
"(0.1, 0.25]"
0.0
"(-0.01, 0.21]"
0.0
"(0.12, 0.25]"
0.0
"(-0.01, 0.25]"
0.0
"(-0.01, 0.2]"
0.0
"(0.13, 0.8]"
0.0
"(-0.01, 0.41]"
0.0
"(-0.01, 0.018]"
0.0
"(0.14, 0.53]"
0.0
"(0.015, 0.058]"
0.0
"(-0.01, 0.66]"
0.0
"(0.89, 1.02]"
0.0
"(0.28, 0.39]"
0.0
"(-0.01, 1.19]"
0.0
"(0.092, 0.18]"
0.0
"(0.11, 0.14]"
0.0
"(0.15, 0.18]"
0.0
"(-0.01, 2.05]"
0.0
"(0.61, 2.68]"
0.0
"(-0.01, 0.53]"
0.0
"(1.23, 1.95]"
0.0
"(1.82, 2.72]"
0.0
"(0.58, 2.34]"
0.0
"(0.36, 0.42]"
0.0
"(0.7, 1.68]"
0.0
"(-0.01, 1.68]"
0.0
"(-0.01, 2.65]"
0.0
"(-0.01, 0.87]"
0.0
"(-0.01, 2.23]"
0.0
"(0.9, 1.48]"
0.0
"(-0.01, 0.14]"
0.0
"(1.35, 2.27]"
0.0
"(0.2, 0.28]"
0.0
"(0.36, 1.06]"
0.0
"(0.3, 0.99]"
0.0
"(-0.01, 1.11]"
0.0
"(0.028, 1.04]"
0.0
"(-0.01, 2.68]"
0.0
"(-0.01, 2.46]"
0.0
"(1.82, 2.19]"
0.0
"(-0.01, 1.97]"
0.0
"(0.48, 2.14]"
0.0
"(0.055, 2.35

In [27]:
bins[k][0]

-0.01

In [28]:
bins_diff = np.array(bins) - val
print(bins_diff)

[[-1.000e-02  2.088e+01]]


In [29]:
bins_diff = np.array([[6, 3, 1], [2, 5, 6], [2, 0, 10]])

In [30]:
np.unravel_index(np.abs(bins_diff).argmin(axis=None), bins_diff.shape)

(2, 1)

In [31]:
instance["original_vector"][j]

0.0

In [32]:
test_dict[0]["scaled_vector"][j]

0.0

In [33]:
row[j]

0.0

In [34]:
bn.variable(feat_list[j-1])

(gum::DiscreteVariable@0x27fa0460) agg__open_cases_sum<"(895.2, 3614.74]">

In [35]:
instance

{'index': 4,
 'original_vector': [27000.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  19.0,
  19.0,
  19.0,
  19.0,
  0.0,
  6.0,
  6.0,
  6.0,
  6.0,
  0.0,
  2.0,
  2.0,
  2.0,
  2.0,
  0.0,
  1158.0,
  1158.0,
  1158.0,
  1158.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  1.0,
  1.0,
  1.0,
  1.0,
  0.0,
  895.0,
  895.0,
  895.0,
  895.0,
  0.0],
 'scaled_vector': [0.2725435716089922,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.

In [36]:
gnb.showInference(bn)

In [37]:
pd.DataFrame(trainingdata, columns=feat_list)

static__AMOUNT_REQ  agg__Activity_A_ACCEPTED-COMPLETE  \
0                0.201819                                0.0   
1                0.050265                                0.0   
2                0.070472                                0.0   
3                0.454408                                0.0   
4                0.151301                                0.0   
...                   ...                                ...   
52117            0.060369                                0.0   
52118            0.060369                                1.0   
52119            0.070472                                0.0   
52120            0.070472                                0.0   
52121            0.070472                                0.0   

       agg__Activity_A_CANCELLED-COMPLETE  agg__Activity_A_DECLINED-COMPLETE  \
0                                     0.0                                0.0   
1                                     0.0                                0.0   
2                                     0.0                                0.0   
3                                     0.0                                0.0   
4                                     0.0                                0.0   
...                                   ...                                ...   
52117                                 0.0                                0.0   
52118                                 0.0                                0.0   
52119                                 0.0                                0.0   
52120                                 0.0                                0.0   
52121                                 0.0                                0.0   

       agg__Activity_A_FINALIZED-COMPLETE  \
0                                     0.0   
1                                     0.0   
2                                     0.0   
3                                     0.0   
4                                     0.0   
...                                   ...   
52117                                 0.0   
52118                                 0.0   
52119                                 0.0   
52120                                 0.0   
52121                                 0.0   

       agg__Activity_A_PARTLYSUBMITTED-COMPLETE  \
0                                           0.0   
1                                           0.0   
2                                           0.0   
3                                           0.0   
4                                           0.0   
...                                         ...   
52117                                       1.0   
52118                                       1.0   
52119                                       1.0   
52120                                       1.0   
52121                                       1.0   

       agg__Activity_A_PREACCEPTED-COMPLETE  \
0                                       0.0   
1                                       0.0   
2                                       0.0   
3                                       0.0   
4                                       0.0   
...                                     ...   
52117                                   1.0   
52118                                   1.0   
52119                                   0.0   
52120                                   1.0   
52121                                   1.0   

       agg__Activity_A_SUBMITTED-COMPLETE  agg__Activity_O_CANCELLED-COMPLETE  \
0                                     0.0                                 0.0   
1                                     0.0                                 0.0   
2                                     0.0                                 0.0   
3                                     0.0                                 0.0   
4                                     0.0                                 0.0   
...                                   ...                               

In [38]:
from pyAgrum.lib.bn2graph import BN2dot, BNinference2dot

g = BNinference2dot(bn, size='"100,10!"', engine=ie)

g.write("bn2graph_test.png", format='png')

True

In [39]:
inference

'<svg xmlns="http://www.w3.org/2000/svg" xmlns:xlink="http://www.w3.org/1999/xlink" width="864pt" height="23pt" viewBox="0.00 0.00 864.00 22.69">\n<g id="graph0" class="graph" transform="scale(16.75 16.75) rotate(0) translate(4 376)">\n<title>structs</title>\n<text text-anchor="middle" x="7230.75" y="-7.8" font-family="Times,serif" font-size="14.00" fill="#4a4a4a">Inference in \xa021.01ms</text>\n<!-- static__AMOUNT_REQ -->\n<g id="node1" class="node">\n<title>static__AMOUNT_REQ</title>\n<polygon fill="#e0e0e0" stroke="#000000" points="2832,-138.5 2641,-138.5 2641,-102.5 2832,-102.5 2832,-138.5"/>\n<svg viewBox="0 0 253.495937 39.408125" width="191px" height="36px" preserveAspectRatio="xMinYMin meet" x="2641" y="-138.5"> <metadata>\n  <rdf:RDF xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:cc="http://creativecommons.org/ns#" xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#">\n   <cc:Work>\n    <dc:type rdf:resource="http://purl.org/dc/dcmitype/StillImage"/>\n    <dc:date>2023-

In [40]:
inference

'<svg xmlns="http://www.w3.org/2000/svg" xmlns:xlink="http://www.w3.org/1999/xlink" width="864pt" height="23pt" viewBox="0.00 0.00 864.00 22.69">\n<g id="graph0" class="graph" transform="scale(16.75 16.75) rotate(0) translate(4 376)">\n<title>structs</title>\n<text text-anchor="middle" x="7230.75" y="-7.8" font-family="Times,serif" font-size="14.00" fill="#4a4a4a">Inference in \xa021.01ms</text>\n<!-- static__AMOUNT_REQ -->\n<g id="node1" class="node">\n<title>static__AMOUNT_REQ</title>\n<polygon fill="#e0e0e0" stroke="#000000" points="2832,-138.5 2641,-138.5 2641,-102.5 2832,-102.5 2832,-138.5"/>\n<svg viewBox="0 0 253.495937 39.408125" width="191px" height="36px" preserveAspectRatio="xMinYMin meet" x="2641" y="-138.5"> <metadata>\n  <rdf:RDF xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:cc="http://creativecommons.org/ns#" xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#">\n   <cc:Work>\n    <dc:type rdf:resource="http://purl.org/dc/dcmitype/StillImage"/>\n    <dc:date>2023-

In [41]:
result_posterior.values[0]

0.2455592628868023

In [42]:
learner = pyAgrum.BNLearner(save_to+"feature_permutations/bpic2012/false_negatives/0_permutations.csv")
bn = learner.learnBN()

IOError: [pyAgrum] I/O Error: File /home/mythreyi/full_stability/bpic2012/logit/single_agg/feature_permutations/bpic2012/false_negatives/0_permutations.csv not found

In [ ]:
num_buckets

In [ ]:
testingdata = all_samples[0]
instance = all_samples[0][0]
trainingdata = all_train[0]

cls = all_cls[0]
scaler = all_scalers[0]

feat_list = [feat.replace(" ", "_") for feat in feature_combiner.get_feature_names()]

class_names = ["Negative", "Positive"]

In [ ]:
lime_explainer = lime.lime_tabular.LimeTabularExplainer(trainingdata,
                                  feature_names = feat_list, class_names=class_names)
if scaler == None:
    exp = lime_explainer.explain_instance(instance, 
                                 cls.predict_proba, num_features=10, labels=[0,1], top_labels=1)
else:
    exp = lime_explainer.explain_instance(instance, 
                             scale_predict_fn, num_features=max_feat, labels=[0,1])

In [ ]:
exp.as_pyplot_figure(0)

In [ ]:
!pip show joblib

In [ ]:
exp.show_in_notebook()

In [ ]:
shap_explainer = shap.Explainer(cls)
explanation = shap_explainer(testingdata)
explanation.feature_names = feat_list
shap.plots.waterfall(explanation[0])

In [ ]:
trainingdata.shape

In [ ]:
np.unique(scaler.inverse_transform(trainingdata), axis=0)

In [ ]:
dataset_manager = DatasetManager(dataset_name)
dataset_manager.static_cat_cols

In [ ]:
trainingdata.shape

In [ ]:
dataset_manager.dynamic_cat_cols

In [ ]:
dataset_manager.static_num_cols

In [ ]:
cats = [feat for col in dataset_manager.dynamic_cat_cols+dataset_manager.static_cat_cols for feat in range(len(feat_list)) if col in feat_list[feat]]

In [ ]:
np.array(feat_list)[cats]